In [2]:
import pandas as pd
import altair as alt
import os
import pprint
from vega_datasets import data
import pycountry

C:\Users\kamin\AppData\Local\Temp\ipykernel_24004\488820849.py:1: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [172]:
# Create dataframes:
coastline_df = pd.read_csv('./data/coastline_lengths.csv', header=1, thousands=',')
ghg_df = pd.read_csv('./data/ghg_EDGAR_country.csv')
co2_df = pd.read_csv('./data/mean_co2_ppm.csv')
sea_level_df = pd.read_csv('./data/sea_level.csv')
# coastline_df.head()
# co2_df.head()
co2_df.head()

year  month  decimal_year  monthly_average    fld4  fld5  fld6  std_dev  \
0  1958      3     1958.2027           315.70  314.43    -1 -9.99     -0.9   
1  1958      4     1958.2877           317.45  315.16    -1 -9.99     -0.9   
2  1958      5     1958.3699           317.51  314.71    -1 -9.99     -0.9   
3  1958      6     1958.4548           317.24  315.14    -1 -9.99     -0.9   
4  1958      7     1958.5370           315.86  315.18    -1 -9.99     -0.9   

   fld8  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   NaN

In [10]:
# zooming and panning
zoom = alt.selection_interval(bind='scales', encodings=['x'])
nearest = alt.selection_point(on='mouseover', nearest=True, empty=False, encodings=['x'])

co2_chart = alt.Chart(co2_df).mark_line().encode(
    y = alt.Y('monthly_average:Q', title='CO2 (ppm)'),
    x = alt.X('decimal_year:Q', title='Year', axis=alt.Axis(format='d', title=None), scale=alt.Scale(domain=[1961, 2023])),
    tooltip=['decimal_year', 'monthly_average']
).add_params(
    zoom
)

# Vertical line
vertical_line = alt.Chart(co2_df).mark_rule(size=4, color='lightgray').encode(
    x='decimal_year:Q',
    opacity=alt.condition(nearest, alt.value(0.7), alt.value(0)),
).add_params(
    nearest
)

interaction_dots = co2_chart.mark_point(size=90, color='firebrick').transform_filter(
    nearest
).encode(
    opacity=alt.condition(nearest, alt.value(1), alt.value(0))
)

text_labels = co2_chart.mark_text(align='left', dx=-40, dy=-15).encode(
    text=alt.condition(nearest, alt.Text('monthly_average:Q', format='.2f'), alt.value(' '))
).transform_filter(
    nearest
)

interactive_co2 = alt.layer(
    co2_chart,
    vertical_line,
    interaction_dots,
    text_labels
).configure_axis(
    labelFontSize=12,
    labelFont='Roboto',
)
interactive_co2


alt.LayerChart(...)

In [21]:
ghg_df.head()

EDGAR Country Code                 Country        1970        1971  \
0                ABW                   Aruba    0.045176    0.050063   
1                AFG             Afghanistan   17.336192   17.292793   
2                AGO                  Angola   20.138364   20.018416   
3                AIA                Anguilla    0.004256    0.004258   
4                AIR  International Aviation  171.160455  171.147982   

         1972        1973        1974        1975        1976        1977  \
0    0.060857    0.065847    0.065108    0.079128    0.078179    0.088896   
1   15.342251   15.966060   17.278443   17.984253   17.989107   18.153414   
2   22.721001   24.375911   25.083208   23.889924   19.960419   24.620945   
3    0.004358    0.004201    0.004451    0.004692    0.004526    0.004627   
4  181.492019  189.261213  182.123246  176.107638  176.412012  192.354128   

   ...        2013        2014        2015        2016        2017  \
0  ...    0.463848    0.475081    0.476461    0.494114    0.467189   
1  ...   30.899954   31.214446   31.208495   30.567230   31.773007   
2  ...   82.985493   85.186645   90.110604   87.096037   81.888045   
3  ...    0.033171    0.033174    0.033318    0.033731    0.034494   
4  ...  488.025465  503.952576  532.878284  555.785220  591.079314   

         2018        2019        2020        2021        2022  
0    0.502077    0.575822    0.494731    0.479192    0.496683  
1   31.439840   30.322851   28.150674   28.953697   29.117879  
2   78.215749   77.435411   71.682513   69.613898   66.480058  
3    0.033631    0.033000    0.028107    0.027267    0.028099  
4  617.430356  627.478302  299.325868  345.376001  425.963735  

[5 rows x 55 columns]

In [127]:
# print(ghg_df.Country.unique())
ghg_df_cleaned = ghg_df[ghg_df['Country'] != 'GLOBAL TOTAL']
ghg_df_cleaned = ghg_df_cleaned.dropna(subset=['Country'])
ghg_df_cleaned = ghg_df_cleaned[ghg_df_cleaned['Country'] != 'EU27']
ghg_df_cleaned = ghg_df_cleaned[ghg_df_cleaned['Country'] != 'International Shipping']
ghg_df_cleaned = ghg_df_cleaned[ghg_df_cleaned['Country'] != 'International Aviation']
ghg_df_cleaned['Country'] = ghg_df_cleaned['Country'].replace('Italy, San Marino and the Holy See', 'Italy')
ghg_df_cleaned['Country'] = ghg_df_cleaned['Country'].replace('Spain and Andorra', 'Spain')
ghg_df_cleaned['Country'] = ghg_df_cleaned['Country'].replace('France and Monaco', 'France')
ghg_df_cleaned['numeric_code'] = ghg_df_cleaned['Country'].apply(lambda x: name_to_numeric(x))
ghg_df_cleaned.head()

SubdivisionHierarchy(code='NL-AW', country_code='NL', name='Aruba', parent_code=None, type='Country')
SubdivisionHierarchy(code='NL-CW', country_code='NL', name='Curaçao', parent_code=None, type='Country')
SubdivisionHierarchy(code='BZ-BZ', country_code='BZ', name='Belize', parent_code=None, type='District')
SubdivisionHierarchy(code='DJ-DJ', country_code='DJ', name='Djibouti', parent_code=None, type='City')
SubdivisionHierarchy(code='US-GA', country_code='US', name='Georgia', parent_code=None, type='State')
SubdivisionHierarchy(code='FR-971', country_code='FR', name='Guadeloupe', parent='GP', parent_code='FR-GP', type='Overseas department')
SubdivisionHierarchy(code='FR-GP', country_code='FR', name='Guadeloupe', parent_code=None, type='Overseas region')
SubdivisionHierarchy(code='GT-GU', country_code='GT', name='Guatemala', parent_code=None, type='Department')
SubdivisionHierarchy(code='BE-WLX', country_code='BE', name='Luxembourg', parent='WAL', parent_code='BE-WAL', type='Province')

EDGAR Country Code      Country       1970       1971       1972       1973  \
0                ABW        Aruba   0.045176   0.050063   0.060857   0.065847   
1                AFG  Afghanistan  17.336192  17.292793  15.342251  15.966060   
2                AGO       Angola  20.138364  20.018416  22.721001  24.375911   
3                AIA     Anguilla   0.004256   0.004258   0.004358   0.004201   
5                ALB      Albania   8.261250   8.205862   9.140924   8.633941   

        1974       1975       1976       1977  ...       2014       2015  \
0   0.065108   0.079128   0.078179   0.088896  ...   0.475081   0.476461   
1  17.278443  17.984253  17.989107  18.153414  ...  31.214446  31.208495   
2  25.083208  23.889924  19.960419  24.620945  ...  85.186645  90.110604   
3   0.004451   0.004692   0.004526   0.004627  ...   0.033174   0.033318   
5   8.906908   9.113707   9.738074  10.293177  ...   9.006529   8.845874   

        2016       2017       2018       2019       2020       2021  \
0   0.494114   0.467189   0.502077   0.575822   0.494731   0.479192   
1  30.567230  31.773007  31.439840  30.322851  28.150674  28.953697   
2  87.096037  81.888045  78.215749  77.435411  71.682513  69.613898   
3   0.033731   0.034494   0.033631   0.033000   0.028107   0.027267   
5   8.461623   9.281257   9.229380   8.744490   7.863104   7.898121   

        2022  numeric_code  
0   0.496683           533  
1  29.117879           004  
2  66.480058           024  
3   0.028099           660  
5   7.983379           008  

[5 rows x 56 columns]

In [128]:
ghg_melted = ghg_df_cleaned.melt(id_vars=["EDGAR Country Code", "Country", "numeric_code"],var_name="Year",value_name="Emissions")
# ghg_melted['Year'].dtypes
ghg_melted['Year'] = ghg_melted['Year'].astype(int)
ghg_melted.head()
# ghg_melted.Country.unique()

EDGAR Country Code      Country numeric_code  Year  Emissions
0                ABW        Aruba          533  1970   0.045176
1                AFG  Afghanistan          004  1970  17.336192
2                AGO       Angola          024  1970  20.138364
3                AIA     Anguilla          660  1970   0.004256
4                ALB      Albania          008  1970   8.261250

In [147]:
alt.data_transformers.disable_max_rows()
max_emissions = max(ghg_melted.Emissions)
year_slider = alt.binding_range(min=1970, max=2022, step=1)
slider_selection = alt.selection_point(bind=year_slider, fields=['Year'], name="Select", value=2022)

ghg_country_chart = alt.Chart(ghg_melted).mark_bar().add_params(
    slider_selection
).transform_filter(
    slider_selection
).transform_window(
    rank='rank(Emissions)',
    sort=[alt.SortField('Emissions', order='descending')],
    groupby=['Year']
).transform_filter(
    alt.datum.rank <= 15
).encode(
    y=alt.Y('Country:N', sort=alt.EncodingSortField(field='Emissions', order='descending'), axis=alt.Axis(title=None)),
    x=alt.X(
        'Emissions:Q',
        title='Mton CO2 equivalent',
        scale=alt.Scale(domain=(0, max_emissions))
    ),
    color=alt.Color('Emissions:Q', legend=alt.Legend(title="Emissions (Mton CO2 eq)"), scale=alt.Scale(domain=(0, max_emissions), scheme='reds')),
    tooltip=['Country', 'Year', 'Emissions']
)

ghg_country_chart

alt.Chart(...)

In [138]:
coastline_df.head()

Country The World Factbook[2] The World Factbook[2].1  \
0            NaN                  Rank                      km   
1  World[Note 2]                     —                 356,000   
2         Canada                     1                 202,080   
3         Norway                     2          83,281[Note 3]   
4      Indonesia                     3                  54,716   

  World Resources Institute[1] World Resources Institute[1].1  \
0                         Rank                             km   
1                            —                      1,634,701   
2                            1                        265,523   
3                            7                         53,199   
4                            4                         95,181   

  Land area  km2 (TWF)[3] Coast/area ratio (m/km2) Coast/area ratio (m/km2).1  \
0                     NaN                    (TWF)                      (WRI)   
1             148,940,000                     2.39                       11.0   
2               9,093,507                     22.2                       29.2   
3                 304,282                      274                        175   
4               1,811,569                     30.2                       52.5   

  Coast/area0.5 ratio  
0               (TWF)  
1                29.2  
2                  67  
3                 151  
4                40.7

In [232]:
coasts = pd.DataFrame(columns=['Country', 'Coastline Length'])
coasts['Country'] = coastline_df['Country']
coasts['Coastline Length'] = coastline_df['The World Factbook[2].1']
coasts['Coast/area (m/km2)'] = coastline_df['Coast/area ratio (m/km2)']
coasts = coasts[1:]
coasts = coasts.dropna(subset=['Country'])
coasts = coasts[coasts['Country'] != 'Jan Mayen']

coasts['Country'] = coasts['Country'].str.replace(r"\[.*?\]", "", regex=True)
coasts['Coastline Length'] = coasts['Coastline Length'].str.replace(r"\[.*?\]", "", regex=True)
coasts = coasts[coasts['Coastline Length'] != 'NA']
coasts = coasts.dropna(subset=['Coastline Length'])

# coasts['Coastline Length'] = coasts['Coastline Length'].astype(int)
coasts['Coastline Length'] = coasts['Coastline Length'].str.replace(',', '').astype(float)

coasts=coasts[coasts['Country'] != 'World']
# print(coasts['Country'].unique())
# set1 = set(coasts['Country'])
# set2 = set(ghg_df_cleaned['Country'])
# set1_unique = set1 - set2
# set2_unique = set2 - set1

# # Print the results
# print(f"Unique to Coasts: {set1_unique}")
# print(f"\nUnique to GHGs: {set2_unique}")
# print(disjoint_set)
coasts.head()
# coasts.to_csv('coasts.csv', index=False) 

Country  Coastline Length Coast/area (m/km2)  numeric_code
2     Canada          202080.0               22.2           NaN
3     Norway           83281.0                274           NaN
4  Indonesia           54716.0               30.2           NaN
5  Greenland           44087.0               20.4           NaN
6     Russia           37653.0               2.30           NaN

In [214]:
coast_rankings = alt.Chart(coasts).mark_bar(   
).transform_window(
    rank = 'rank(Coastline Length)',
    sort = [alt.SortField('Coastline Length',order='descending')]
).transform_filter(
    alt.datum.rank <= 15
).encode(
    y = alt.Y('Country:N', sort=alt.EncodingSortField(field='Coastline Length', order='descending'), axis=alt.Axis(title=None)),
    x = alt.X('Coastline Length:Q', title='Coastline Length (km)')
)
coast_rankings | ghg_country_chart

alt.HConcatChart(...)

In [234]:
def name_to_iso_alpha3(country_name):
    try:
        return pycountry.countries.search_fuzzy(country_name)[0].alpha_3
        # return pycountry.countries.lookup(country_name).alpha_3
    except LookupError:
        return -1

def name_to_numeric(country_name):
    try:
        # print(country_name)
        return pycountry.countries.search_fuzzy(country_name)[0].numeric
    except LookupError:
        return -1
coasts['iso_a3'] = coasts['Country'].apply(lambda x: name_to_iso_alpha3(x))
coasts['numeric_code'] = coasts['Country'].apply(lambda x: name_to_numeric(x))

# coasts = coasts[coasts['iso_a3'] != -1]
# RUS, TUR, BHS, PRK, KOR, CIV
coasts.head()


SubdivisionHierarchy(code='MX-MEX', country_code='MX', name='México', parent_code=None, type='State')
SubdivisionHierarchy(code='PA-8', country_code='PA', name='Panamá', parent_code=None, type='Province')
SubdivisionHierarchy(code='US-MP', country_code='US', name='Northern Mariana Islands', parent_code=None, type='Outlying area')
SubdivisionHierarchy(code='US-PR', country_code='US', name='Puerto Rico', parent_code=None, type='Outlying area')
SubdivisionHierarchy(code='GT-GU', country_code='GT', name='Guatemala', parent_code=None, type='Department')
SubdivisionHierarchy(code='BZ-BZ', country_code='BZ', name='Belize', parent_code=None, type='District')
SubdivisionHierarchy(code='NL-CW', country_code='NL', name='Curaçao', parent_code=None, type='Country')
SubdivisionHierarchy(code='DJ-DJ', country_code='DJ', name='Djibouti', parent_code=None, type='City')
SubdivisionHierarchy(code='US-GA', country_code='US', name='Georgia', parent_code=None, type='State')
SubdivisionHierarchy(code='US-GU'

Country  Coastline Length Coast/area (m/km2) numeric_code iso_a3
2     Canada          202080.0               22.2          124    CAN
3     Norway           83281.0                274          578    NOR
4  Indonesia           54716.0               30.2          360    IDN
5  Greenland           44087.0               20.4          304    GRL
6     Russia           37653.0               2.30          643    RUS

In [235]:
coasts['numeric_code'] = coasts['numeric_code'].str.lstrip('0')
coasts.loc[coasts['Country'] == 'Turkey', 'numeric_code'] = 792
coasts.loc[coasts['Country'] == 'Bahamas, The', 'numeric_code'] = 44
coasts.loc[coasts['Country'] == 'Korea, North', 'numeric_code'] = 408
coasts.loc[coasts['Country'] == 'Korea, South', 'numeric_code'] = 410
coasts.loc[coasts['Country'] == 'CÃ´te d\'Ivoire (Ivory Coast)', 'numeric_code'] = 384
coasts.loc[coasts['Country'] == 'Congo, Republic of the', 'numeric_code'] = 178
coasts.loc[coasts['Country'] == 'Congo, Democratic Republic of the', 'numeric_code'] = 180
coasts.loc[coasts['Country'] == 'Niger', 'numeric_code'] = 562
coasts.loc[coasts['Coastline Length'] == 364.0, 'numeric_code'] = 531 # fix curacao

print(coasts[coasts['Country'] == 'Congo, Republic of the'])

                    Country  Coastline Length Coast/area (m/km2) numeric_code  \
148  Congo, Republic of the             169.0              0.495          178   

    iso_a3  
148     -1  


In [236]:
coasts.to_csv('./data/coasts_countries.csv', index=False)

In [64]:
import requests
import json

# Get the URL from vega_datasets
world_url = data.world_110m.url

# Download the TopoJSON data
response = requests.get(world_url)
topojson_data = response.json()

# Assuming the objects are called 'countries' as per your code
# This will print out the first few 'id' values in the 'countries' object
countries = topojson_data['objects']['countries']['geometries']
ids = [geo['id'] for geo in data.world_110m()['objects']['countries']['geometries']]
# pprint.pprint(data.world_110m()['objects']['countries']['geometries'])
print(ids)

[4, 24, 8, 784, 32, 51, 10, 260, 36, 40, 31, 108, 56, 204, 854, 50, 100, 44, 70, 112, 84, 68, 76, 96, 64, 72, 140, 124, 756, 152, 156, 384, 120, 180, 178, 170, 188, 192, -99, 196, 203, 276, 262, 208, 214, 12, 218, 818, 232, 724, 233, 231, 246, 242, 238, 250, 266, 826, 268, 288, 324, 270, 624, 226, 300, 304, 320, 328, 340, 191, 332, 348, 360, 356, 372, 364, 368, 352, 376, 380, 388, 400, 392, 398, 404, 417, 116, 410, -99, 414, 418, 422, 430, 434, 144, 426, 440, 442, 428, 504, 498, 450, 484, 807, 466, 104, 499, 496, 508, 478, 454, 458, 516, 540, 562, 566, 558, 528, 578, 524, 554, 512, 586, 591, 604, 608, 598, 616, 630, 408, 620, 600, 275, 634, 642, 643, 646, 732, 682, 729, 728, 686, 90, 694, 222, -99, 706, 688, 740, 703, 705, 752, 748, 760, 148, 768, 764, 762, 795, 626, 780, 788, 792, 158, 834, 800, 804, 858, 840, 860, 862, 704, 548, 887, 710, 894, 716]


In [237]:
from vega_datasets import data
world = data.world_110m.url
countries = alt.topo_feature(world, 'countries')

selection = alt.selection_point(fields=['Country'], empty=False, value=840)

choro = alt.Chart(countries).mark_geoshape(
    stroke='#aaa', strokeWidth=0.25
).transform_lookup(
    # lookup='id', from_=alt.LookupData(data=coasts, key='id', fields=['Country','Coastline Length'])
    lookup='id',from_=alt.LookupData(data=coasts, key='numeric_code', fields=['Country', 'Coastline Length'])
).encode(
    alt.Color('Coastline Length:Q', scale=alt.Scale(type='sqrt',scheme='yellowgreenblue'), legend=alt.Legend(title='Coastline Length (km)')),
    # opacity=alt.condition(selection, alt.value(1), alt.value(0.5)),
    tooltip=['Country:N','Coastline Length:Q']
).project(
    type='equalEarth'
).properties(
    width=600,
    height=500
)

choro

alt.Chart(...)

In [238]:
coast_per_area = alt.Chart(countries).mark_geoshape(
    stroke='#aaa', strokeWidth=0.25
).transform_lookup(
    # lookup='id', from_=alt.LookupData(data=coasts, key='id', fields=['Country','Coastline Length'])
    lookup='id',from_=alt.LookupData(data=coasts, key='numeric_code', fields=['Country', 'Coast/area (m/km2)'])
).encode(
    alt.Color('Coast/area (m/km2):Q', scale=alt.Scale(type='sqrt',scheme='yellowgreenblue'), legend=alt.Legend(title='Coast/area ratio (m/km2)')),
    tooltip=['Country:N','Coast/area (m/km2):Q']
).project(
    type='equalEarth'
).properties(
    width=600,
    height=500
)
coast_per_area

alt.Chart(...)

In [240]:
vertical = (choro & coast_per_area).resolve_scale(
    color='independent'
)
vertical

alt.VConcatChart(...)

In [170]:
ghg_melted = ghg_melted.dropna(subset=['Emissions'])
year_slider2 = alt.binding_range(min=1970, max=2022, step=1)
slider_selection2 = alt.selection_point(bind=year_slider2, fields=['Year'], name="Select", value=2022)

choro_emissions = alt.Chart(countries).mark_geoshape(
    stroke='#aaa', strokeWidth=0.25
).add_params(
    slider_selection2
).transform_lookup(
    lookup='id',from_=alt.LookupData(data=ghg_melted, key='numeric_code', fields=['Country', 'Emissions', 'Year'])
).add_params(
    slider_selection2
).encode(
    alt.Color('Emissions:Q', scale=alt.Scale(scheme='reds'), legend=alt.Legend()),
    tooltip = ['Country:N', 'Emissions:Q', 'Year:Q']
).project(
    type='equalEarth'
).properties(
    width=600,
    height=500
)

choro_emissions

alt.Chart(...)

In [177]:
sea_level_df.rename(columns={"fld3": "decimal_year", "fld6": "GMSL_mm"}, inplace=True)
sea_level_df.head()

fld1  fld2  decimal_year    fld4       fld5  GMSL_mm   fld7   fld8   fld9  \
0     0    11   1993.011526  466881  338409.69   -37.91  89.01 -37.67 -37.90   
1     0    12   1993.038692  459563  333609.59   -40.95  89.95 -39.07 -40.94   
2     0    13   1993.065858  402996  292736.50   -41.09  86.90 -39.11 -41.07   
3     0    14   1993.093025  462894  336670.31   -43.38  88.73 -39.40 -43.36   
4     0    15   1993.120191  460498  332486.09   -38.66  89.87 -38.51 -38.63   

   fld10  fld11  fld12  fld13  
0  89.01 -37.66 -37.64  -37.6  
1  89.95 -39.06 -38.53  -38.5  
2  86.90 -39.09 -38.16  -38.1  
3  88.73 -39.38 -38.12  -38.1  
4  89.87 -38.48 -36.96  -37.0

In [195]:
# zooming and panning
zoom2 = alt.selection_interval(bind='scales', encodings=['x'])
nearest2 = alt.selection_point(on='mouseover', nearest=True, empty=False, encodings=['x'])

sea_level_chart = alt.Chart(sea_level_df).mark_line().encode(
    y = alt.Y('GMSL_mm:Q', title='Global Mean Sea Level Variation (mm)'),
    x = alt.X('decimal_year:Q', title='Year', axis=alt.Axis(format='d', title=None), scale=alt.Scale(domain=[1995, 2023])),
    # tooltip=['decimal_year:Q', 'GMSL_mm:Q']
    tooltip=alt.value(None),
).add_params(
    zoom2
)
# sea_level_chart
line = alt.Chart(sea_level_df).mark_rule(size=4, color='lightgray').encode(
    x='decimal_year:Q',
    opacity=alt.condition(nearest2, alt.value(0.7), alt.value(0)),
).add_params(
    nearest2
)

points = sea_level_chart.mark_point(size=90, color='firebrick').transform_filter(
    nearest2
).encode(
    opacity=alt.condition(nearest2, alt.value(1), alt.value(0))
)

labels = sea_level_chart.mark_text(align='left', dx=-40, dy=-15).encode(
    text=alt.condition(nearest2, alt.Text('GMSL_mm:Q', format='.2f'), alt.value(' '))
).transform_filter(
    nearest2
)

interactive_sea_level = alt.layer(
    sea_level_chart,
    line,
    points,
    labels
)
interactive_sea_level


alt.LayerChart(...)